In [1]:
import numpy as np
import scipy.stats as stats
from tqdm import tnrange, tqdm_notebook

from allensdk.core.brain_observatory_cache import BrainObservatoryCache

#Plotting tools
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import Scatter, Figure, Layout,Bar

from force import NeuralNetwork
from force import Simulation


init_notebook_mode(connected=True)

ImportError: No module named 'allensdk'

In [115]:
boc = BrainObservatoryCache(manifest_file='/Users/elijahc/dev/allen-assistant/boc/manifest.json')
#boc = BrainObservatoryCache(manifest_file='/home/elijahc/dev/tools/allen-assistant/boc/manifest.json')

exps = boc.get_ophys_experiments(
    imaging_depths=[175],
    targeted_structures=['VISp'],
    cre_lines=['Cux2-CreERT2'],
    stimuli=['natural_scenes'])

In [152]:
import scipy.stats as stats
from allensdk.brain_observatory.dff import movingaverage, movingmode_fast
exp_id = exps[1]['id']
data_set = boc.get_ophys_experiment_data(exp_id)
cids = data_set.get_cell_specimen_ids()
num_cells=50
print('%d Cells in Experiment %d'%(len(cids),exp_id))
idxs = data_set.get_spontaneous_activity_stimulus_table()
#idxs = data_set.get_stimulus_table('natural_scenes')

t,ftr = data_set.get_corrected_fluorescence_traces(cell_specimen_ids=cids[0:100])
#t,ftr = data_set.get_dff_traces(cell_specimen_ids=cids[0:num_cells])

t = t[idxs.start.item():idxs.end.item()]
ftr_crop = ftr[:,idxs.start.item():idxs.end.item()]

dt = t - np.roll(t,1)


214 Cells in Experiment 500964514
(100,)
(100, 8902)


In [106]:
net = NeuralNetwork(N=500,dt=0.03318,num_fits=num_cells)
sim = Simulation(network=net,dt=0.03318)
zt = []
rPrt = []
dwt = []
#pretrain_steps= 600
train_steps = 5000
test_steps = 3000
ft0 = np.repeat(ftr_crop[:,:1],pretrain_steps,axis=1)
ft_cat = np.concatenate([ft0,ftr_crop],axis=1)

for epoch in np.arange(4):
    for i in tqdm_notebook(
        sim.iter(steps=train_steps,ft=ftr_crop,train=True,learn_every=3),
        total=train_steps,desc='Training'):
        if i > 1:
            rPrt.append(sim.network.rPr)
            dwt.append(np.power(sim.network.dw,2).sum())
   
for i in tqdm_notebook(
    sim.iter(steps=train_steps,ft=ftr_crop,train=True),
    total=train_steps,desc='Training',postfix={'dw':dwt[-1]}):
    zt.append(sim.network.z)
    rPrt.append(sim.network.rPr)
    dwt.append(np.power(sim.network.dw,2).sum())
    
for i in tqdm_notebook(
    sim.iter(steps=test_steps,ft=ftr_crop[:,train_steps:],train=False),
    total=test_steps,desc='Predicting'):
    
    zt.append(sim.network.z)        
    dwt.append(np.power(sim.network.dw,2).sum())
zt = np.squeeze(np.array(zt))
rPrt = np.squeeze(np.array(rPrt))
dwt = np.squeeze(np.array(dwt))


#iplot([{'y':rPrt}])
iplot([{'y':dwt,}])

[[ 0.17044969  0.00275272 -0.00175695 ..., -0.00031738 -0.01111454
   0.00344607]
 [ 0.00275272  0.20960183  0.00201185 ..., -0.00577961  0.02375389
   0.00778103]
 [-0.00175695  0.00201185  0.14345931 ...,  0.00259308  0.01064159
   0.00407889]
 ..., 
 [-0.00031738 -0.00577961  0.00259308 ...,  0.17736988  0.00767421
   0.008395  ]
 [-0.01111454  0.02375389  0.01064159 ...,  0.00767421  0.16699269
  -0.00026095]
 [ 0.00344607  0.00778103  0.00407889 ...,  0.008395   -0.00026095
   0.14494208]]


In [111]:
pcorr = []
fevs = []
for i in np.arange(num_cells):
    f,z = sim.ft[i,:test_steps],zt[train_steps:,i]
    R,_ = stats.pearsonr(f,z)
    pcorr.append(R)
    
    se = np.power((f-z),2)
    fevs.append(1-(se.mean()/np.var(f)))

df_layout = Layout(
    title='Force Layout Default Title',
    xaxis=dict(
        title='Time(s)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='dF/F (a.u.)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
)

pcorr_layout = Layout(
    title='Pearson Corr. Coef. by Cell',
    xaxis=dict(
        title='Cell idx',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='Pearson Corr. Coef. (R)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
)
d = Bar(y=pcorr)
fig = Figure(data=[d],layout=pcorr_layout)
print(np.mean(pcorr))
iplot(fig)
iplot([{'y':fevs}])
idx=35
iplot([{'x':t,'y':ftr_crop[idx,:]},
       {'x':t[:train_steps],'y':zt[:train_steps,idx]},
      {'x':t[train_steps:],'y':zt[train_steps:,idx]}])

0.028524545327


In [109]:
idx=np.argmin(pcorr)
data=[{'x':t,'y':ftr_crop[idx,:],'name':'True f(t)'},
       {'x':t[:train_steps],'y':zt[:train_steps,idx],'name':'Train z(t)'},
      {'x':t[train_steps:],'y':zt[train_steps:,idx],'name':'Test z(t)'}]
df_layout.title='Least Correlated'
worse_fig = Figure(data=data,layout=df_layout)
iplot(worse_fig)

In [110]:
idx=np.argmax(pcorr)
best_dat=[{'x':t,'y':ftr_crop[idx,:],'name':'True f(t)'},
       {'x':t[:train_steps],'y':zt[:train_steps,idx],'name':'Train z(t)'},
      {'x':t[train_steps:],'y':zt[train_steps:,idx],'name':'Test z(t)'}]
df_layout.title='Most Correlated'
best_fig = Figure(data=best_dat,layout=df_layout)
iplot(best_fig)

In [ ]:
idx=76
best_dat=[{'x':t,'y':ftr_crop[idx,:],'name':'True f(t)'},
       {'x':t[:train_steps],'y':zt[:train_steps,idx],'name':'Train z(t)'},
      {'x':t[train_steps:],'y':zt[train_steps:,idx],'name':'Test z(t)'}]
df_layout.title='Example'
best_fig = Figure(data=best_dat,layout=df_layout)
iplot(best_fig)

In [ ]:
dxcm,dxtim = data_set.get_running_speed()
dxcm = dxcm[idxs.start.item():idxs.end.item()]
iplot([{'y':dxcm}])